# Capstone Project - The Battle of the Neighborhoods (Week 2)
Applied Data Science Capstone by IBM/Coursera

# Table of contents


1.Introduction: Business Problem


2.Data 

 3.Methodology

 4.Analysis

 5.Observation

# 1.Introduction: Business Problem

In this project we will try to find an location for a restaurant.

Since there are lots of restaurants in Toronto we will try to detect locations that are not already crowded with restaurants. We are also particularly interested in areas with no Indian restaurants in vicinity. We would also prefer locations as close to city center as possible, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders. this report will be targeted to stakeholders interested in opening an Italian restaurant in Toronto.

# 2.Data

number of existing restaurants in the neighborhood (any type of restaurant) number of and distance to Italian restaurants in the neighborhood, if any distance of neighborhood from city center We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:

centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using Google Maps API reverse geocoding number of restaurants and their type and location in every neighborhood will be obtained using Foursquare API coordinate of Delhi center will be obtained using Google Maps API geocoding of well known toronto location.

# 3.Methodology

# Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:

import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


# Downloading the data for segmentation
Use the Notebook to build the code to scrape the following Wikipedia page, https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M, in order to obtain the data that is in the table of postal codes and to transform the data into a pandas dataframe like the one shown below:

To create the dataframe: The dataframe will consist of three columns: PostalCode, Borough, and Neighborhood. Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned. More than one neighborhood can exist in one postal code area. For example, in the table on the Wikipedia page, you will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma as shown in row 11 in the above table. If a cell has a borough but a Not assigned neighborhood, then the neighborhood will be the same as the borough. So for the 9th cell in the table on the Wikipedia page, the value of the Borough and the Neighborhood columns will be Queen's Park. Clean your Notebook and add Markdown cells to explain your work and any assumptions you are making. In the last cell of your notebook, use the .shape method to print the number of rows of your dataframe. Note: There are different website scraping libraries and packages in Python. One of the most common packages is BeautifulSoup. Here is the package's main documentation page: http://beautiful-soup-4.readthedocs.io/en/latest/

In [2]:
#install Beautiful Soup 
!pip install BeautifulSoup4
!pip install requests

# GET DATA
now for downloading the data we will follow three steps first we will start with get html from wikipedia then we will Use BeautifySoup to parse html data and then store parsed data into Pandas DataFrame

1.get HTML from wikipedia



In [3]:
from bs4 import BeautifulSoup
s1=requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
soup = BeautifulSoup(s1.text, 'lxml')


2.use soup for parsing the data

In [4]:
d = []
col = []
table = soup.find(class_='wikitable')
for index, tr in enumerate(table.find_all('tr')):
    section = []
    for td in tr.find_all(['th','td']):
        section.append(td.text.rstrip())
    
    #First row of data is the header
    if (index == 0):
        col = section
    else:
        d.append(section)

3.covert parse data to pandas dataframe

In [5]:
df = pd.DataFrame(data = d,columns = col)
df.head()

Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

# data wrangling

In [6]:
#Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned
df1=df[df['Borough']!='Not assigned']
df1.head()

Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

More than one neighborhood can exist in one postal code area. For example, in the table on the Wikipedia page, you will notice that M5A is listed twice and has two neighborhoods: Harbourfront and Regent Park. These two rows will be combined into one row with the neighborhoods separated with a comma as shown in row 11 in the above table.

In [7]:
df1["Neighbourhood"] =df1.groupby("Postal Code")["Neighbourhood"].transform(lambda neigh: ', '.join(neigh))

#remove duplicates
df1= df1.drop_duplicates()


if(df1.index.name != 'Postal Code'):
    df1 = df1.set_index('Postal Code')
    
df1.head()

    
df1.head()

C:\Users\DELL PC\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


Borough                                Neighbourhood
Postal Code                                                               
M3A                North York                                    Parkwoods
M4A                North York                             Victoria Village
M5A          Downtown Toronto                    Regent Park, Harbourfront
M6A                North York             Lawrence Manor, Lawrence Heights
M7A          Downtown Toronto  Queen's Park, Ontario Provincial Government

In [8]:
df1['Neighbourhood'].replace("Not assigned", df1["Borough"],inplace=True)
df1.head()

Borough                                Neighbourhood
Postal Code                                                               
M3A                North York                                    Parkwoods
M4A                North York                             Victoria Village
M5A          Downtown Toronto                    Regent Park, Harbourfront
M6A                North York             Lawrence Manor, Lawrence Heights
M7A          Downtown Toronto  Queen's Park, Ontario Provincial Government

In [9]:
df1.shape

(103, 2)

I will use the csv file downloaded

In [10]:
df_geo_coor = pd.read_csv("Desktop/Geospatial_Coordinates.csv")
df_geo_coor.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [11]:
#we need to have dataframe that contain both the data frames df1 and df_geo_coor so here it is

df_t = pd.merge(df1, df_geo_coor, on = 'Postal Code')
df_t.shape

(103, 5)

In [12]:
df_t.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [13]:
df2=df_t.drop(['Postal Code'],axis=1)
df2.head()

Borough                                Neighbourhood   Latitude  \
0        North York                                    Parkwoods  43.753259   
1        North York                             Victoria Village  43.725882   
2  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
3        North York             Lawrence Manor, Lawrence Heights  43.718518   
4  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   

   Longitude  
0 -79.329656  
1 -79.315572  
2 -79.360636  
3 -79.464763  
4 -79.389494

In [14]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df2['Borough'].unique()),
        df2.shape[0]
    )
)

The dataframe has 10 boroughs and 103 neighborhoods.


In [15]:
#count Bourough and Neighborhood
df2.groupby('Borough').count()['Neighbourhood']

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
East York            5
Etobicoke           12
Mississauga          1
North York          24
Scarborough         17
West Toronto         6
York                 5
Name: Neighbourhood, dtype: int64

In [16]:
df3= df2[df2['Borough'].str.contains("Toronto")].reset_index(drop=True)
df3.head()

Borough                                Neighbourhood   Latitude  \
0  Downtown Toronto                    Regent Park, Harbourfront  43.654260   
1  Downtown Toronto  Queen's Park, Ontario Provincial Government  43.662301   
2  Downtown Toronto                     Garden District, Ryerson  43.657162   
3  Downtown Toronto                               St. James Town  43.651494   
4      East Toronto                                  The Beaches  43.676357   

   Longitude  
0 -79.360636  
1 -79.389494  
2 -79.378937  
3 -79.375418  
4 -79.293031

In [17]:
#Check the number of neighborhoods
print(df3.groupby('Borough').count()['Neighbourhood'])

Borough
Central Toronto      9
Downtown Toronto    19
East Toronto         5
West Toronto         6
Name: Neighbourhood, dtype: int64


lets plot a map

In [18]:

#Get the latitude and longitude values of Toronto.
address = "Toronto, ON"

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto city are {}, {}.'.format(latitude, longitude))







# create map using latitude and longitude values
map_t1= folium.Map(location=[latitude,longitude], zoom_start=10)
map_t1

for lat, lng, borough, neighborhood in zip(df3['Latitude'], df3['Longitude'], df3['Borough'], df3['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_t1)  

map_t1


The geograpical coordinate of Toronto city are 43.6534817, -79.3839347.


In [19]:
#Define Foursquare Credentials and Version

CLIENT_ID = ''
CLIENT_SECRET = ''
VERSION = ''
radius=500
LIMIT=100

In [24]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [25]:
#Now write the code to run the above function on each neighborhood and create a new dataframe called toronto_denc_venues

toronto_denc_venues = getNearbyVenues(names=df3['Neighbourhood'],
                                   latitudes=df3['Latitude'],
                                   longitudes=df3['Longitude']
                                  )


Regent Park, Harbourfront
Queen's Park, Ontario Provincial Government
Garden District, Ryerson
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
The Danforth West, Riverdale
Toronto Dominion Centre, Design Exchange
Brockton, Parkdale Village, Exhibition Place
India Bazaar, The Beaches West
Commerce Court, Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North & West, Forest Hill Road Park
High Park, The Junction South
North Toronto West,  Lawrence Park
The Annex, North Midtown, Yorkville
Parkdale, Roncesvalles
Davisville
University of Toronto, Harbord
Runnymede, Swansea
Moore Park, Summerhill East
Kensington Market, Chinatown, Grange Park
Summerhill West, Rathnelly, South Hill, Forest Hill SE, Deer Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport


In [26]:
toronto_denc_venues.head()


Neighbourhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Regent Park, Harbourfront               43.65426              -79.360636   
1  Regent Park, Harbourfront               43.65426              -79.360636   
2  Regent Park, Harbourfront               43.65426              -79.360636   
3  Regent Park, Harbourfront               43.65426              -79.360636   
4  Regent Park, Harbourfront               43.65426              -79.360636   

                    Venue  Venue Latitude  Venue Longitude  \
0        Roselle Desserts       43.653447       -79.362017   
1           Tandem Coffee       43.653559       -79.361809   
2  Cooper Koo Family YMCA       43.653249       -79.358008   
3     Body Blitz Spa East       43.654735       -79.359874   
4          Impact Kitchen       43.656369       -79.356980   

        Venue Category  
0               Bakery  
1          Coffee Shop  
2  Distribution Center  
3                  Spa  
4           Restaurant

In [27]:
toronto_denc_venues.groupby('Neighbourhood').count()

Neighborhood Latitude  \
Neighbourhood                                                               
Berczy Park                                                            57   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre, South Ce...                     15   
CN Tower, King and Spadina, Railway Lands, Harb...                     15   
Central Bay Street                                                     64   
Christie                                                               17   
Church and Wellesley                                                   76   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             33   
Davisville North                                                       10   
Dufferin, Dovercourt Village                                           18   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          26   
India Bazaar, The Beaches West                                         19   
Kensington Market, Chinatown, Grange Park                              68   
Lawrence Park                                                           3   
Little Portugal, Trinity                                               44   
Moore Park, Summerhill East                                             2   
North Toronto West,  Lawrence Park                                     19   
Parkdale, Roncesvalles                                                 14   
Queen's Park, Ontario Provincial Government                            34   
Regent Park, Harbourfront                                              43   
Richmond, Adelaide, King                                              100   
Rosedale                                                                4   
Roselawn                                                                2   
Runnymede, Swansea                                                     34   
St. James Town                                                         84   
St. James Town, Cabbagetown                                            45   
Stn A PO Boxes                                                         97   
Studio District                                                        41   
Summerhill West, Rathnelly, South Hill, Forest ...                     16   
The Annex, North Midtown, Yorkville                                    21   
The Beaches                                                             4   
The Danforth West, Riverdale                                           42   
Toronto Dominion Centre, Design Exchange                              100   
University of Toronto, Harbord                                         35   

                                                    Neighborhood Longitude  \
Neighbourhood                                                                
Berczy Park                                                             57   
Brockton, Parkdale Village, Exhibition Place                            22   
Business reply mail Processing Centre, South Ce...                      15   
CN Tower, King and Spadina, Railway Lands, Harb...                      15   
Central Bay Street                                                      64   
Christie                                                                17   
Church and Wellesley                                                    76   
Commerce Court, Victoria Hotel                                         100   
Davisville                                                              33   
Davisville North                    

In [28]:
print('There are {} uniques categories.'.format(len(toronto_denc_venues['Venue Category'].unique())))

There are 234 uniques categories.


In [30]:
#print out the list of categories
toronto_denc_venues['Venue Category'].unique()[:100]

array(['Bakery', 'Coffee Shop', 'Distribution Center', 'Spa',
       'Restaurant', 'Park', 'Historic Site', 'Breakfast Spot',
       'Gym / Fitness Center', 'Pub', 'Farmers Market', 'Chocolate Shop',
       'Performing Arts Venue', 'Dessert Shop', 'Theater',
       'French Restaurant', 'Mexican Restaurant', 'Café', 'Yoga Studio',
       'Event Space', 'Shoe Store', 'Ice Cream Shop', 'Cosmetics Shop',
       'Electronics Store', 'Bank', 'Beer Store', 'Antique Shop',
       'Portuguese Restaurant', 'Italian Restaurant', 'Sushi Restaurant',
       'Persian Restaurant', 'Creperie', 'Beer Bar',
       'Arts & Crafts Store', 'Hobby Shop', 'Japanese Restaurant',
       'Diner', 'Fried Chicken Joint', 'Smoothie Shop', 'Sandwich Place',
       'College Auditorium', 'Gym', 'Bar', 'College Cafeteria',
       'Art Gallery', 'Clothing Store', 'Comic Shop', 'Plaza',
       'Pizza Place', 'Burrito Place', 'Music Venue', 'Burger Joint',
       'Thai Restaurant', 'Movie Theater', 'College Rec Center',


In [32]:
# check if the results contain "Italian Restaurants"

"Italian Restaurant" in toronto_denc_venues['Venue Category'].unique()

True

# Analizing Neighbourhood

In [33]:
# one hot encoding
toronto_denc_onehot = pd.get_dummies(toronto_denc_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_denc_onehot['Neighbourhood'] = toronto_denc_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_denc_onehot.columns[-1]] + list(toronto_denc_onehot.columns[:-1])
toronto_denc_onehot = toronto_denc_onehot[fixed_columns]

toronto_denc_onehot.head()

Neighbourhood  Afghan Restaurant  Airport  Airport Food Court  \
0  Regent Park, Harbourfront                  0        0                   0   
1  Regent Park, Harbourfront                  0        0                   0   
2  Regent Park, Harbourfront                  0        0                   0   
3  Regent Park, Harbourfront                  0        0                   0   
4  Regent Park, Harbourfront                  0        0                   0   

   Airport Lounge  Airport Service  Airport Terminal  American Restaurant  \
0               0                0                 0                    0   
1               0                0                 0                    0   
2               0                0                 0                    0   
3               0                0                 0                    0   
4               0                0                 0                    0   

   Antique Shop  Aquarium  Art Gallery  Art Museum  Arts & Crafts Store  \
0             0         0            0           0                    0   
1             0         0            0           0                    0   
2             0         0            0           0                    0   
3             0         0            0           0                    0   
4             0         0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Baby Store  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  Basketball Stadium  Beach  \
0           0       1     0    0                 0                   0      0   
1           0       0     0    0                 0                   0      0   
2           0       0     0    0                 0                   0      0   
3           0       0     0    0                 0                   0      0   
4           0       0     0    0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bistro  \
0                0         0           0                   0       0   
1                0         0           0                   0       0   
2                0         0           0                   0       0   
3                0         0           0                   0       0   
4                0         0           0                   0       0   

   Boat or Ferry  Bookstore  Boutique  Brazilian Restaurant  Breakfast Spot  \
0              0          0         0                     0               0   
1              0          0         0                     0               0   
2              0          0         0                     0               0   
3              0          0         0                     0               0   
4              0          0         0                     0               0   

   Brewery  Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0        0                0         0             0              0         0   
1        0                0         0             0              0         0   
2        0                0         0             0              0         0   
3        0                0         0             0              0         0   
4        0                0         0             0              0         0   

   Butcher  Café  Cajun / Creole Restaurant  Camera Store  Candy Store  \
0        0     0                          0             0            0   
1        0     0                          0             0            0   
2        0     0                   

In [34]:
#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

toronto_denc_grouped = toronto_denc_onehot.groupby('Neighbourhood').mean().reset_index()
toronto_denc_grouped.head()

Neighbourhood  Afghan Restaurant  \
0                                        Berczy Park                0.0   
1       Brockton, Parkdale Village, Exhibition Place                0.0   
2  Business reply mail Processing Centre, South C...                0.0   
3  CN Tower, King and Spadina, Railway Lands, Har...                0.0   
4                                 Central Bay Street                0.0   

    Airport  Airport Food Court  Airport Lounge  Airport Service  \
0  0.000000            0.000000        0.000000         0.000000   
1  0.000000            0.000000        0.000000         0.000000   
2  0.000000            0.000000        0.000000         0.000000   
3  0.066667            0.066667        0.133333         0.133333   
4  0.000000            0.000000        0.000000         0.000000   

   Airport Terminal  American Restaurant  Antique Shop  Aquarium  Art Gallery  \
0          0.000000                  0.0           0.0       0.0     0.017544   
1          0.000000                  0.0           0.0       0.0     0.000000   
2          0.000000                  0.0           0.0       0.0     0.000000   
3          0.133333                  0.0           0.0       0.0     0.000000   
4          0.000000                  0.0           0.0       0.0     0.000000   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0    0.000000                  0.0               0.0                 0.0   
1    0.000000                  0.0               0.0                 0.0   
2    0.000000                  0.0               0.0                 0.0   
3    0.000000                  0.0               0.0                 0.0   
4    0.015625                  0.0               0.0                 0.0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop    Bakery  Bank       Bar  \
0       0.000000   0.017544         0.0    0.017544  0.035088   0.0  0.000000   
1       0.000000   0.000000         0.0    0.000000  0.045455   0.0  0.045455   
2       0.066667   0.000000         0.0    0.000000  0.000000   0.0  0.000000   
3       0.000000   0.000000         0.0    0.000000  0.000000   0.0  0.000000   
4       0.000000   0.000000         0.0    0.000000  0.000000   0.0  0.015625   

   Baseball Stadium  Basketball Stadium     Beach  Bed & Breakfast  Beer Bar  \
0               0.0            0.017544  0.017544              0.0  0.035088   
1               0.0            0.000000  0.000000              0.0  0.000000   
2               0.0            0.000000  0.000000              0.0  0.000000   
3               0.0            0.000000  0.000000              0.0  0.000000   
4               0.0            0.000000  0.000000              0.0  0.000000   

   Beer Store  Belgian Restaurant    Bistro  Boat or Ferry  Bookstore  \
0         0.0                 0.0  0.017544       0.000000        0.0   
1         0.0                 0.0  0.000000       0.000000        0.0   
2         0.0                 0.0  0.000000       0.000000        0.0   
3         0.0                 0.0  0.000000       0.066667        0.0   
4         0.0                 0.0  0.000000       0.000000        0.0   

   Boutique  Brazilian Restaurant  Breakfast Spot   Brewery  Bubble Tea Shop  \
0  0.000000                   0.0        0.017544  0.000000          0.00000   
1  0.000000                   0.0        0.090909  0.000000          0.00000   
2  0.000000                   0.0        0.000000  0.066667          0.00000   
3  0.066667                   0.0        0.000000  0.000000          0.00000   
4  0.000000                   0.0        0.000000  0.000000          0.03125   

   Building  Burger Joint  Burrito Place  Bus Line  Butcher      Café  \
0       0.0       0.00000       0.000000       0.0      0.0  0.035088   
1       0.0       0.00000       0.045455       0.0      0.0  0.136364   
2       0.0       0.00000       0.066667       0.0      0.0  0.000000   
3       0.0       0.00000       0.000000       0.0     

In [36]:
len(toronto_denc_grouped[toronto_denc_grouped["Italian Restaurant"] > 0])

22

In [61]:
#Create a new dataframe to find italian Restaurants only

italian=toronto_denc_grouped[["Neighbourhood","Italian Restaurant"]]
italian.head()

it=pd.merge(italian, toronto_denc_venues, on = 'Neighbourhood')
it.head()



Neighbourhood  Italian Restaurant  Neighborhood Latitude  \
0   Berczy Park            0.017544              43.644771   
1   Berczy Park            0.017544              43.644771   
2   Berczy Park            0.017544              43.644771   
3   Berczy Park            0.017544              43.644771   
4   Berczy Park            0.017544              43.644771   

   Neighborhood Longitude                                 Venue  \
0              -79.373306  The Keg Steakhouse + Bar - Esplanade   
1              -79.373306                                  LCBO   
2              -79.373306                        Fresh On Front   
3              -79.373306                         Meridian Hall   
4              -79.373306                         Biff's Bistro   

   Venue Latitude  Venue Longitude                 Venue Category  
0       43.646712       -79.374768                     Restaurant  
1       43.642944       -79.372440                   Liquor Store  
2       43.647815       -79.374453  Vegetarian / Vegan Restaurant  
3       43.646292       -79.376022                   Concert Hall  
4       43.647085       -79.376342              French Restaurant

## 4.Analysis

# Cluster Neighborhoods
Run k-means to cluster the neighborhoods in Toronto into 5 clusters.

In [63]:
# set number of clusters
toclusters = 5

to_clustering = italian.drop(["Neighbourhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 2, 1, 1, 2, 3, 1, 0, 3, 1])

In [64]:
#Check the 10 most common venues in each neighborhood.

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_denc_grouped['Neighbourhood']

for ind in np.arange(toronto_denc_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_denc_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood 1st Most Common Venue  \
0                                        Berczy Park           Coffee Shop   
1       Brockton, Parkdale Village, Exhibition Place                  Café   
2  Business reply mail Processing Centre, South C...    Light Rail Station   
3  CN Tower, King and Spadina, Railway Lands, Har...        Airport Lounge   
4                                 Central Bay Street           Coffee Shop   

  2nd Most Common Venue 3rd Most Common Venue   4th Most Common Venue  \
0          Cocktail Bar                Bakery      Seafood Restaurant   
1           Coffee Shop        Breakfast Spot  Furniture / Home Store   
2         Auto Workshop                  Park              Comic Shop   
3       Airport Service      Airport Terminal                Boutique   
4        Sandwich Place                  Café      Italian Restaurant   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0        Farmers Market            Restaurant           Cheese Shop   
1          Intersection    Italian Restaurant                   Bar   
2           Pizza Place      Recording Studio            Restaurant   
3               Airport    Airport Food Court      Sculpture Garden   
4      Department Store   Japanese Restaurant          Burger Joint   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                  Café              Beer Bar       Department Store  
1                Bakery            Restaurant           Climbing Gym  
2         Burrito Place               Brewery             Skate Park  
3       Harbor / Marina   Rental Car Location          Boat or Ferry  
4       Bubble Tea Shop           Salad Place  Portuguese Restaurant

In [65]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_denc_merged = it


toronto_denc_merged = toronto_denc_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_denc_merged.head() # check the last columns!

Neighbourhood  Italian Restaurant  Neighborhood Latitude  \
0   Berczy Park            0.017544              43.644771   
1   Berczy Park            0.017544              43.644771   
2   Berczy Park            0.017544              43.644771   
3   Berczy Park            0.017544              43.644771   
4   Berczy Park            0.017544              43.644771   

   Neighborhood Longitude                                 Venue  \
0              -79.373306  The Keg Steakhouse + Bar - Esplanade   
1              -79.373306                                  LCBO   
2              -79.373306                        Fresh On Front   
3              -79.373306                         Meridian Hall   
4              -79.373306                         Biff's Bistro   

   Venue Latitude  Venue Longitude                 Venue Category  \
0       43.646712       -79.374768                     Restaurant   
1       43.642944       -79.372440                   Liquor Store   
2       43.647815       -79.374453  Vegetarian / Vegan Restaurant   
3       43.646292       -79.376022                   Concert Hall   
4       43.647085       -79.376342              French Restaurant   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0               0           Coffee Shop          Cocktail Bar   
1               0           Coffee Shop          Cocktail Bar   
2               0           Coffee Shop          Cocktail Bar   
3               0           Coffee Shop          Cocktail Bar   
4               0           Coffee Shop          Cocktail Bar   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                Bakery    Seafood Restaurant        Farmers Market   
1                Bakery    Seafood Restaurant        Farmers Market   
2                Bakery    Seafood Restaurant        Farmers Market   
3                Bakery    Seafood Restaurant        Farmers Market   
4                Bakery    Seafood Restaurant        Farmers Market   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0            Restaurant           Cheese Shop                  Café   
1            Restaurant           Cheese Shop                  Café   
2            Restaurant           Cheese Shop                  Café   
3            Restaurant           Cheese Shop                  Café   
4            Restaurant           Cheese Shop                  Café   

  9th Most Common Venue 10th Most Common Venue  
0              Beer Bar       Department Store  
1              Beer Bar       Department Store  
2              Beer Bar       Department Store  
3              Beer Bar       Department Store  
4              Beer Bar       Department Store

In [67]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i + x + (i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(
        toronto_denc_merged['Neighborhood Latitude'], 
        toronto_denc_merged['Neighborhood Longitude'], 
        toronto_denc_merged['Neighbourhood'], 
        toronto_denc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster),parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [68]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

## Examine Clusters
# cluster 0
 
 


In [94]:
#Cluster 0
toronto_denc_merged[toronto_denc_merged['Cluster Labels'] == 0]

Neighbourhood  Italian Restaurant  \
0                                           Berczy Park            0.017544   
1                                           Berczy Park            0.017544   
2                                           Berczy Park            0.017544   
3                                           Berczy Park            0.017544   
4                                           Berczy Park            0.017544   
5                                           Berczy Park            0.017544   
6                                           Berczy Park            0.017544   
7                                           Berczy Park            0.017544   
8                                           Berczy Park            0.017544   
9                                           Berczy Park            0.017544   
10                                          Berczy Park            0.017544   
11                                          Berczy Park            0.017544   
12                                          Berczy Park            0.017544   
13                                          Berczy Park            0.017544   
14                                          Berczy Park            0.017544   
15                                          Berczy Park            0.017544   
16                                          Berczy Park            0.017544   
17                                          Berczy Park            0.017544   
18                                          Berczy Park            0.017544   
19                                          Berczy Park            0.017544   
20                                          Berczy Park            0.017544   
21                                          Berczy Park            0.017544   
22                                          Berczy Park            0.017544   
23                                          Berczy Park            0.017544   
24                                          Berczy Park            0.017544   
25                                          Berczy Park            0.017544   
26                                          Berczy Park            0.017544   
27                                          Berczy Park            0.017544   
28                                          Berczy Park            0.017544   
29                                          Berczy Park            0.017544   
30                                          Berczy Park            0.017544   
31                                          Berczy Park            0.017544   
32                                          Berczy Park            0.017544   
33                                          Berczy Park            0.017544   
34                                          Berczy Park            0.017544   
35                                          Berczy Park            0.017544   
36                                          Berczy Park            0.017544   
37                                          Berczy Park            0.017544   
38                                          Berczy Park            0.017544   
39                                          Berczy Park            0.017544   
40                                          Berczy Park            0.017544   
41                                          Berczy Park            0.017544   
42                                          Berczy Park            0.017544   
43                                          Berczy Park            0.017544   
44                                          Berczy Park            0.017544   
45                                          Berczy Park            0.017544   
46                                          Berczy Park            0.017544   
47                                          Berczy Park            0.017544   
48                                          Berczy Park            0.017544   
49                                          Berczy Park            0.017544   
50           

# cluster 1

In [96]:
#Cluster 1
toronto_denc_merged.loc[toronto_denc_merged['Cluster Labels'] == 1]

Neighbourhood  Italian Restaurant  \
79    Business reply mail Processing Centre, South C...                0.00   
80    Business reply mail Processing Centre, South C...                0.00   
81    Business reply mail Processing Centre, South C...                0.00   
82    Business reply mail Processing Centre, South C...                0.00   
83    Business reply mail Processing Centre, South C...                0.00   
84    Business reply mail Processing Centre, South C...                0.00   
85    Business reply mail Processing Centre, South C...                0.00   
86    Business reply mail Processing Centre, South C...                0.00   
87    Business reply mail Processing Centre, South C...                0.00   
88    Business reply mail Processing Centre, South C...                0.00   
89    Business reply mail Processing Centre, South C...                0.00   
90    Business reply mail Processing Centre, South C...                0.00   
91    Business reply mail Processing Centre, South C...                0.00   
92    Business reply mail Processing Centre, South C...                0.00   
93    Business reply mail Processing Centre, South C...                0.00   
94    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
95    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
96    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
97    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
98    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
99    CN Tower, King and Spadina, Railway Lands, Har...                0.00   
100   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
101   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
102   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
103   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
104   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
105   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
106   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
107   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
108   CN Tower, King and Spadina, Railway Lands, Har...                0.00   
190                                Church and Wellesley                0.00   
191                                Church and Wellesley                0.00   
192                                Church and Wellesley                0.00   
193                                Church and Wellesley                0.00   
194                                Church and Wellesley                0.00   
195                                Church and Wellesley                0.00   
196                                Church and Wellesley                0.00   
197                                Church and Wellesley                0.00   
198                                Church and Wellesley                0.00   
199                                Church and Wellesley                0.00   
200                                Church and Wellesley                0.00   
201                                Church and Wellesley                0.00   
202                                Church and Wellesley                0.00   
203                                Church and Wellesley                0.00   
204                                Church and Wellesley                0.00   
205                                Church and Wellesley                0.00   
206                                Church and Wellesley                0.00   
207                                Church and Wellesley                0.00   
208                                Church and Wellesley                0.00   
209                                Church and Wellesley                0.00   
210          

# cluster 2

In [97]:
#Cluster 2
toronto_denc_merged.loc[toronto_denc_merged['Cluster Labels'] == 2]

Neighbourhood  Italian Restaurant  \
57    Brockton, Parkdale Village, Exhibition Place            0.045455   
58    Brockton, Parkdale Village, Exhibition Place            0.045455   
59    Brockton, Parkdale Village, Exhibition Place            0.045455   
60    Brockton, Parkdale Village, Exhibition Place            0.045455   
61    Brockton, Parkdale Village, Exhibition Place            0.045455   
62    Brockton, Parkdale Village, Exhibition Place            0.045455   
63    Brockton, Parkdale Village, Exhibition Place            0.045455   
64    Brockton, Parkdale Village, Exhibition Place            0.045455   
65    Brockton, Parkdale Village, Exhibition Place            0.045455   
66    Brockton, Parkdale Village, Exhibition Place            0.045455   
67    Brockton, Parkdale Village, Exhibition Place            0.045455   
68    Brockton, Parkdale Village, Exhibition Place            0.045455   
69    Brockton, Parkdale Village, Exhibition Place            0.045455   
70    Brockton, Parkdale Village, Exhibition Place            0.045455   
71    Brockton, Parkdale Village, Exhibition Place            0.045455   
72    Brockton, Parkdale Village, Exhibition Place            0.045455   
73    Brockton, Parkdale Village, Exhibition Place            0.045455   
74    Brockton, Parkdale Village, Exhibition Place            0.045455   
75    Brockton, Parkdale Village, Exhibition Place            0.045455   
76    Brockton, Parkdale Village, Exhibition Place            0.045455   
77    Brockton, Parkdale Village, Exhibition Place            0.045455   
78    Brockton, Parkdale Village, Exhibition Place            0.045455   
109                             Central Bay Street            0.046875   
110                             Central Bay Street            0.046875   
111                             Central Bay Street            0.046875   
112                             Central Bay Street            0.046875   
113                             Central Bay Street            0.046875   
114                             Central Bay Street            0.046875   
115                             Central Bay Street            0.046875   
116                             Central Bay Street            0.046875   
117                             Central Bay Street            0.046875   
118                             Central Bay Street            0.046875   
119                             Central Bay Street            0.046875   
120                             Central Bay Street            0.046875   
121                             Central Bay Street            0.046875   
122                             Central Bay Street            0.046875   
123                             Central Bay Street            0.046875   
124                             Central Bay Street            0.046875   
125                             Central Bay Street            0.046875   
126                             Central Bay Street            0.046875   
127                             Central Bay Street            0.046875   
128                             Central Bay Street            0.046875   
129                             Central Bay Street            0.046875   
130                             Central Bay Street            0.046875   
131                             Central Bay Street            0.046875   
132                             Central Bay Street            0.046875   
133                             Central Bay Street            0.046875   
134                             Central Bay Street            0.046875   
135                             Central Bay Street            0.046875   
136                             Central Bay Street            0.046875   
137                             Central Bay Street            0.046875   
138                             Central Bay Street            0.046875   
139                             Central Bay Street            0.046875   
140                             Central B

# cluster 3

In [98]:
#Cluster 3
toronto_denc_merged.loc[toronto_denc_merged['Cluster Labels'] == 3]

Neighbourhood  Italian Restaurant  \
173                         Christie            0.058824   
174                         Christie            0.058824   
175                         Christie            0.058824   
176                         Christie            0.058824   
177                         Christie            0.058824   
178                         Christie            0.058824   
179                         Christie            0.058824   
180                         Christie            0.058824   
181                         Christie            0.058824   
182                         Christie            0.058824   
183                         Christie            0.058824   
184                         Christie            0.058824   
185                         Christie            0.058824   
186                         Christie            0.058824   
187                         Christie            0.058824   
188                         Christie            0.058824   
189                         Christie            0.058824   
366                       Davisville            0.060606   
367                       Davisville            0.060606   
368                       Davisville            0.060606   
369                       Davisville            0.060606   
370                       Davisville            0.060606   
371                       Davisville            0.060606   
372                       Davisville            0.060606   
373                       Davisville            0.060606   
374                       Davisville            0.060606   
375                       Davisville            0.060606   
376                       Davisville            0.060606   
377                       Davisville            0.060606   
378                       Davisville            0.060606   
379                       Davisville            0.060606   
380                       Davisville            0.060606   
381                       Davisville            0.060606   
382                       Davisville            0.060606   
383                       Davisville            0.060606   
384                       Davisville            0.060606   
385                       Davisville            0.060606   
386                       Davisville            0.060606   
387                       Davisville            0.060606   
388                       Davisville            0.060606   
389                       Davisville            0.060606   
390                       Davisville            0.060606   
391                       Davisville            0.060606   
392                       Davisville            0.060606   
393                       Davisville            0.060606   
394                       Davisville            0.060606   
395                       Davisville            0.060606   
396                       Davisville            0.060606   
397                       Davisville            0.060606   
398                       Davisville            0.060606   
757   India Bazaar, The Beaches West            0.052632   
758   India Bazaar, The Beaches West            0.052632   
759   India Bazaar, The Beaches West            0.052632   
760   India Bazaar, The Beaches West            0.052632   
761   India Bazaar, The Beaches West            0.052632   
762   India Bazaar, The Beaches West            0.052632   
763   India Bazaar, The Beaches West            0.052632   
764   India Bazaar, The Beaches West            0.052632   
765   India Bazaar, The Beaches West            0.052632   
766   India Bazaar, The Beaches West            0.052632   
767   India Bazaar, The Beaches West            0.052632   
768   India Bazaar, The Beaches West            0.052632   
769   India Bazaar, The Beaches West            0.052632   
770   India Bazaar, The Beaches West            0.052632   
771   India Bazaar, The Beaches West            0.052632   
772   India Bazaar, The Beaches West            0.052632   
773

# cluster 4

In [99]:
#Cluster 4
toronto_denc_merged.loc[toronto_denc_merged['Cluster Labels'] == 4]


Neighbourhood  Italian Restaurant  Neighborhood Latitude  \
912         Parkdale, Roncesvalles            0.071429              43.648960   
913         Parkdale, Roncesvalles            0.071429              43.648960   
914         Parkdale, Roncesvalles            0.071429              43.648960   
915         Parkdale, Roncesvalles            0.071429              43.648960   
916         Parkdale, Roncesvalles            0.071429              43.648960   
917         Parkdale, Roncesvalles            0.071429              43.648960   
918         Parkdale, Roncesvalles            0.071429              43.648960   
919         Parkdale, Roncesvalles            0.071429              43.648960   
920         Parkdale, Roncesvalles            0.071429              43.648960   
921         Parkdale, Roncesvalles            0.071429              43.648960   
922         Parkdale, Roncesvalles            0.071429              43.648960   
923         Parkdale, Roncesvalles            0.071429              43.648960   
924         Parkdale, Roncesvalles            0.071429              43.648960   
925         Parkdale, Roncesvalles            0.071429              43.648960   
1451  The Danforth West, Riverdale            0.071429              43.679557   
1452  The Danforth West, Riverdale            0.071429              43.679557   
1453  The Danforth West, Riverdale            0.071429              43.679557   
1454  The Danforth West, Riverdale            0.071429              43.679557   
1455  The Danforth West, Riverdale            0.071429              43.679557   
1456  The Danforth West, Riverdale            0.071429              43.679557   
1457  The Danforth West, Riverdale            0.071429              43.679557   
1458  The Danforth West, Riverdale            0.071429              43.679557   
1459  The Danforth West, Riverdale            0.071429              43.679557   
1460  The Danforth West, Riverdale            0.071429              43.679557   
1461  The Danforth West, Riverdale            0.071429              43.679557   
1462  The Danforth West, Riverdale            0.071429              43.679557   
1463  The Danforth West, Riverdale            0.071429              43.679557   
1464  The Danforth West, Riverdale            0.071429              43.679557   
1465  The Danforth West, Riverdale            0.071429              43.679557   
1466  The Danforth West, Riverdale            0.071429              43.679557   
1467  The Danforth West, Riverdale            0.071429              43.679557   
1468  The Danforth West, Riverdale            0.071429              43.679557   
1469  The Danforth West, Riverdale            0.071429              43.679557   
1470  The Danforth West, Riverdale            0.071429              43.679557   
1471  The Danforth West, Riverdale            0.071429              43.679557   
1472  The Danforth West, Riverdale            0.071429              43.679557   
1473  The Danforth West, Riverdale            0.071429              43.679557   
1474  The Danforth West, Riverdale            0.071429              43.679557   
1475  The Danforth West, Riverdale            0.071429              43.679557   
1476  The Danforth West, Riverdale            0.071429              43.679557   
1477  The Danforth West, Riverdale            0.071429              43.679557   
1478  The Danforth West, Riverdale            0.071429              43.679557   
1479  The Danforth West, Riverdale            0.071429              43.679557   
1480  The Danforth West, Riverdale            0.071429              43.679557   
1481  The Danforth West, Riverdale            0.071429              43.679557   
1482  The Danforth West, Riverdale            0.071429              43.679557   
1483  The Danforth West, Riverdale            0.071429              43.679557   
1484  The Danforth West, Riverdale            0.071429              43.679557   
1485  The Danforth West, Riverdale            0.0714

# Observations
Most of Italian restaurants are in Cluster 0  and lowest in Cluster 4 and cluster 2  areas. Also, there are good opportunities to open restrurant in parkside drive and bayview avenue bloor street areas as the competition seems to be low. Looking at nearby venues, it seems Cluster 4 might be a good location as there are not a lot of italian restaurants in these areas. Therefore, this project recommends the entrepreneur to open an authentic Burmese restaurant in these locations with little to no competition. Nonetheless, if the food is authentic, affordable and good taste, I am confident that it will have great following everywhere.